In [1]:
import re
import os, sys
sys.path.append(os.path.abspath('../../'))
import pandas as pd
import numpy as np
from datetime import datetime
from EMAWorkbench import Policy
from EMAWorkbench.em_framework import sample_uncertainties
from EMAWorkbench import SequentialEvaluator, ema_logging, save_results, load_results


def evaluation(model, problem, random_seed, steps, policy_path, result_path, real_num=False):
    the_model, _ = model(problem=problem, random_seed=random_seed)

    ea_policies = pd.read_csv(policy_path)
    policies = []
    for index, row in ea_policies.iterrows():
        if real_num:
            policy = Policy(str(index), **{str(i):row[str(i)] for i in range(steps)})
        else:
            policy = Policy(str(index), **{str(i):int(row[str(i)]) for i in range(steps)})
        policies.append(policy)
        
    ema_logging.log_to_stderr(ema_logging.INFO)
    current_time = datetime.now().strftime("%d-%m-%Y-%H-%M")

    if not os.path.exists(result_path):
        os.makedirs(result_path)
    
    i = 0
    for policy in policies:
        with SequentialEvaluator(the_model) as evaluator:
            results = evaluator.perform_experiments(policies=policy)

        save_results(results, result_path+f'{current_time}_{i}.tar.gz')
        i += 1
    return results

In [2]:
def robustness_evaluation(model, problem, random_seed, steps, scenarios_num, 
                          scenario_path, policy_path, result_path, real_num=False):
    the_model, _ = model(problem=problem, random_seed=random_seed)
    
    evaluation_df_read = pd.read_csv(scenario_path)
    evaluation_scenarios_designs = list(evaluation_df_read.to_records(index=False))
    evaluation_scenarios = sample_uncertainties(the_model, scenarios_num)
    evaluation_scenarios.designs = evaluation_scenarios_designs

    ea_policies = pd.read_csv(policy_path)
    policies = []
    for index, row in ea_policies.iterrows():
        if real_num:
            policy = Policy(str(index), **{str(i):row[str(i)] for i in range(steps)})
        else:
            policy = Policy(str(index), **{str(i):int(row[str(i)]) for i in range(steps)})
        policies.append(policy)
        
    ema_logging.log_to_stderr(ema_logging.INFO)
    current_time = datetime.now().strftime("%d-%m-%Y-%H-%M")
    
    if not os.path.exists(result_path):
        os.makedirs(result_path)

    i = 0
    for policy in policies:
        with SequentialEvaluator(the_model) as evaluator:
            results = evaluator.perform_experiments(scenarios=evaluation_scenarios, policies=policy)

        save_results(results, result_path+f'{current_time}_{i}.tar.gz')
        i += 1
    return results

# Discrete Dam Problem

In [3]:
from models.ema_dam import dam_problem
from utils.ea.create_models import create_dam_discrete_training

policy_path = '../../results/ea_dam_1/'
files=sorted(os.listdir(policy_path))
files

['.DS_Store',
 'discrete_2_1274569960-17-11-2022-06-17_convergence.csv',
 'discrete_2_1274569960-17-11-2022-06-17_policy.csv',
 'discrete_2_1350287007-17-11-2022-06-27_convergence.csv',
 'discrete_2_1350287007-17-11-2022-06-27_policy.csv',
 'discrete_2_1883682950-17-11-2022-06-34_convergence.csv',
 'discrete_2_1883682950-17-11-2022-06-34_policy.csv',
 'discrete_2_1926216712-17-11-2022-06-10_convergence.csv',
 'discrete_2_1926216712-17-11-2022-06-10_policy.csv',
 'discrete_2_2097286424-17-11-2022-06-19_convergence.csv',
 'discrete_2_2097286424-17-11-2022-06-19_policy.csv',
 'discrete_2_2523200676-17-11-2022-06-15_convergence.csv',
 'discrete_2_2523200676-17-11-2022-06-15_policy.csv',
 'discrete_2_2861224539-17-11-2022-06-25_convergence.csv',
 'discrete_2_2861224539-17-11-2022-06-25_policy.csv',
 'discrete_2_3087161096-17-11-2022-06-12_convergence.csv',
 'discrete_2_3087161096-17-11-2022-06-12_policy.csv',
 'discrete_2_3186775264-17-11-2022-06-04_convergence.csv',
 'discrete_2_3186775264

In [4]:
for i in range(2, len(files), 2):
    seed = re.split("_|-", files[i])[2]
    evaluation(model=create_dam_discrete_training, problem=dam_problem, random_seed=1793476144, steps=100,
               policy_path=f'{policy_path}{files[i]}',
               result_path=f'../../results/dam_discrete_performance_2/ea_{seed}/')

[MainProcess/INFO] performing 1 scenarios * 1 policies * 1 model(s) = 1 experiments
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191:

# Robust Dam Problem (deep)

In [5]:
from models.ema_dam_uncertain import dam_uncertain_problem
from utils.ea.create_models import create_dam_deep_training


policy_path = '../../results/ea_dam_deep_1/'
files=sorted(os.listdir(policy_path))
files

['.DS_Store',
 '10th_20_1274569960-20-11-2022-06-10_convergence.csv',
 '10th_20_1274569960-20-11-2022-06-10_policy.csv',
 '10th_20_1350287007-20-11-2022-20-56_convergence.csv',
 '10th_20_1350287007-20-11-2022-20-56_policy.csv',
 '10th_20_1883682950-21-11-2022-08-45_convergence.csv',
 '10th_20_1883682950-21-11-2022-08-45_policy.csv',
 '10th_20_1926216712-19-11-2022-18-23_convergence.csv',
 '10th_20_1926216712-19-11-2022-18-23_policy.csv',
 '10th_20_2097286424-20-11-2022-09-07_convergence.csv',
 '10th_20_2097286424-20-11-2022-09-07_policy.csv',
 '10th_20_2523200676-20-11-2022-03-13_convergence.csv',
 '10th_20_2523200676-20-11-2022-03-13_policy.csv',
 '10th_20_2861224539-20-11-2022-17-58_convergence.csv',
 '10th_20_2861224539-20-11-2022-17-58_policy.csv',
 '10th_20_3087161096-19-11-2022-21-20_convergence.csv',
 '10th_20_3087161096-19-11-2022-21-20_policy.csv',
 '10th_20_3186775264-19-11-2022-05-42_convergence.csv',
 '10th_20_3186775264-19-11-2022-05-42_policy.csv',
 '10th_20_3186775264-19

In [6]:
for i in range(2, len(files), 2):
    tmp = re.split("_|-", files[i])
    r_metric = tmp[0]
    seed = tmp[2]
    robustness_evaluation(model=create_dam_deep_training, problem=dam_uncertain_problem, 
                          random_seed=1793476144, steps=100, scenarios_num=1000,
                          scenario_path="../../results/dam_scenarios/evaluation_scenarios.csv",
                          policy_path=f'{policy_path}{files[i]}',
                          result_path=f'../../results/dam_deep_performance_2/ea_{r_metric}_{seed}/')

[MainProcess/INFO] performing 1000 scenarios * 1 policies * 1 model(s) = 1000 experiments
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.p

# Discrete Lake Problem

In [3]:
from models.ema_lake import lake_problem
from utils.ea.create_models import create_lake_discrete_training

policy_path = '../../results/ea_lake_1/'
files=sorted(os.listdir(policy_path))
files

['discrete_200_1274569960-29-11-2022-00-06_convergence.csv',
 'discrete_200_1274569960-29-11-2022-00-06_policy.csv',
 'discrete_200_1350287007-29-11-2022-11-08_convergence.csv',
 'discrete_200_1350287007-29-11-2022-11-08_policy.csv',
 'discrete_200_1883682950-29-11-2022-19-25_convergence.csv',
 'discrete_200_1883682950-29-11-2022-19-25_policy.csv',
 'discrete_200_1926216712-28-11-2022-16-20_convergence.csv',
 'discrete_200_1926216712-28-11-2022-16-20_policy.csv',
 'discrete_200_2097286424-29-11-2022-02-05_convergence.csv',
 'discrete_200_2097286424-29-11-2022-02-05_policy.csv',
 'discrete_200_2523200676-28-11-2022-22-10_convergence.csv',
 'discrete_200_2523200676-28-11-2022-22-10_policy.csv',
 'discrete_200_2861224539-29-11-2022-08-52_convergence.csv',
 'discrete_200_2861224539-29-11-2022-08-52_policy.csv',
 'discrete_200_3087161096-28-11-2022-18-16_convergence.csv',
 'discrete_200_3087161096-28-11-2022-18-16_policy.csv',
 'discrete_200_3186775264-28-11-2022-10-32_convergence.csv',
 'd

In [ ]:
for i in range(1, len(files), 2):
    seed = re.split("_|-", files[i])[2]
    evaluation(model=create_lake_discrete_training, problem=lake_problem, random_seed=1793476144, steps=99,
               policy_path=f'{policy_path}{files[i]}',
               result_path=f'../../results/lake_discrete_performance_2/ea_{seed}/')

[MainProcess/INFO] performing 1 scenarios * 1 policies * 1 model(s) = 1 experiments
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
[MainProcess/INFO] performing experiments sequentially
[MainProcess/INFO] 1 cases completed
[Mai

# Robust Lake Problem

In [ ]:
from models.ema_lake_uncertain import lake_uncertain_problem
from utils.ea.create_models import create_lake_deep_training


policy_path = '../../results/ea_lake_robust_1/'
files=sorted(os.listdir(policy_path))
files

In [ ]:
for i in range(1, len(files), 2):
    tmp = re.split("_|-", files[i])
    r_metric = tmp[0]
    seed = tmp[2]
    robustness_evaluation(model=create_lake_deep_training, problem=lake_uncertain_problem, 
                          random_seed=1793476144, steps=99, scenarios_num=1000,
                          scenario_path="../../results/lake_scenarios/evaluation_scenarios.csv",
                          policy_path=f'{policy_path}{files[i]}',
                          result_path=f'../../results/lake_robust_performance_2/ea_{r_metric}_{seed}/')

[MainProcess/INFO] 600 cases completed
[MainProcess/INFO] 700 cases completed
[MainProcess/INFO] 800 cases completed
[MainProcess/INFO] 900 cases completed
[MainProcess/INFO] 1000 cases completed
[MainProcess/INFO] experiments finished
[MainProcess/INFO] results saved successfully to /Users/zppei/Documents/PhD-Project/code/Evolutionary/results/lake_robust_performance_2/ea_10th_1350287007/13-03-2023-23-06_31.tar.gz
[MainProcess/INFO] performing 1000 scenarios * 1 policies * 1 model(s) = 1000 experiments
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/cal